In [1]:
import numpy as np
import scipy.signal as sig
import bokeh.plotting as bkp
import bokeh.models as bkm
bkp.output_notebook()

from asl_bloch_sim import bloch, rf_design

<frozen importlib._bootstrap>:228: RuntimeWarning: scipy._lib.messagestream.MessageStream size changed, may indicate binary incompatibility. Expected 56 from C header, got 64 from PyObject


Loading BokehJS ...

In [2]:
duration = 2 # seconds
dt = 0.0001 # seconds

flip_angle = 180 # degrees
rf_duration = 0.040 # seconds
rf_bandwidth = 250 # Hz
off_resonance = 500 # Hz
spectrum_lines = 5000

T1 = 1.5 # seconds
T2 = 0.1 # seconds

In [3]:
time = np.arange(0, duration, dt) # seconds
rf_time = np.arange(-rf_duration / 2, rf_duration / 2, dt)

rf_pulse = rf_design.sinc_pulse(flip_angle, rf_duration, rf_bandwidth, dt)
rf = rf_design.extend(rf_pulse, duration, dt)

dfz = np.linspace(0, off_resonance, spectrum_lines) # Hz
dBz = dfz / bloch.GAMMA_BAR # T

B = np.moveaxis([np.zeros(rf.shape + dBz.shape),
                 *np.broadcast_arrays(np.expand_dims(rf, 1), dBz)], 0, -1)

In [4]:
# plot RF with bokeh
plot = bkp.figure(width=800, height=400, title='RF pulse')
plot.line(rf_time * 1e3, rf_pulse * 1e6, line_width=2)
plot.xaxis.axis_label = 'Time (ms)'
plot.yaxis.axis_label = 'RF Amplitude (µT)'
bkp.show(plot)

In [5]:
mag = np.array([[0, 0, 1]]) # initial magnetization
mags = np.array([mag := bloch.relax(bloch.precess(mag, B[step], dt), T1, T2, dt) for step in range(round(duration / dt))])

In [6]:
# plot magnetization with bokeh
plot = bkp.figure(width=800, height=400, title='Magnetization')
plot.line(time, mags[:, 12, 0], line_width=2, legend_label='Mx', alpha=0.5)
plot.line(time, mags[:, 12, 1], line_width=2, legend_label='My', color='orange', alpha=0.5)
plot.line(time, mags[:, 12, 2], line_width=2, legend_label='Mz', color='green')
plot.xaxis.axis_label = 'Time (s)'
plot.yaxis.axis_label = 'Magnetization (a.u.)'
plot.x_range = bkm.DataRange1d(start=0, end=0.14)
bkp.show(plot)

In [7]:
# plot magnetization off-resonances with bokeh
title = 'Longitudinal Magnetization with Off-Resonance Pulse'
plot = bkp.figure(width=1000, height=500, title=title)
for offres in range(0, end := mags.shape[1], end // 10):
    alpha = 1 - offres / end
    plot.line(time, mags[:, offres, 2], line_width=2, legend_label=f'{dfz[offres]:g} Hz',
              alpha=alpha, color='green')
plot.xaxis.axis_label = 'Time (s)'
plot.yaxis.axis_label = 'Magnetization (a.u.)'
plot.x_range = bkm.DataRange1d(start=0.01, end=0.05)
bkp.show(plot)

In [8]:
flipped = np.argmin(mags[:, 0, 2], axis=0)
plot = bkp.figure(width=800, height=400, title='Flipped Magnetization Spectrum')
plot.line(dfz, mags[flipped, :, 2], line_width=2)
plot.xaxis.axis_label = 'Off-Resonance Frequency (Hz)'
plot.yaxis.axis_label = 'Magnetization (a.u.)'
bkp.show(plot)